# Julia Mistakes To Avoid
_Emi Soroka, Fall 2021. Developed for Julia 1.6.0._

**Why write the bug in the first place if you know you have to get rid of it?**<br>
In this notebook you will learn to avoid some common errors. Don't feel bad if you've made these errors in the past: everyone does. But please try to avoid them in the future.

## 1. Dimension Mismatch
Many students, on seeing this error

```DimensionMismatch("A has dimensions (3,4) but B has dimensions (3,3)")```

are tempted to sprinkle transposes throughout their code hoping it will go away. **This is a very bad idea.**

DimensionMismatch is the coding equivalent of a **crime against matrices**: a capital offence that will not be tolerated in EE263 (or 364). http://ee263.stanford.edu/notes/matrix_crimes.pdf<br>
By randomly transposing variables, you hope to cover up the crime. Unfortunately covering up a crime is much more difficult than not committing one in the first place. It will probably return to bite you later.

### Example 1
While solving a problem, you get confused with some matrix dimensions and form the expression $AB$ when $A\in\mathbb{R}^{3\times 4}$ and $B\in \mathbb{R}^{3\times 3}$. (This is, of course, a crime against matrices.)

You attempt to implement your solution in Julia, but receive a...**DIMENSION ERROR!**

In [1]:
using LinearAlgebra, Plots
A = rand(3,4)
B = rand(3,3)

A*B # Dimension error!

LoadError: DimensionMismatch("A has dimensions (3,4) but B has dimensions (3,3)")

It's tempting to transpose $A$, $B$, or both, hoping to make the error go away. In fact, you might stumble on writing
$$A^\top B$$
which does run.
But this isn't the expression you wrote while solving the problem. In covering up the matrix crime, you have lost an opportunity to catch a serious error.

### Example 2
You are multiplying a diagonal matrix by a non-diagonal matrix. This comes up all the time: for example in the expression $A = U\Sigma V^\top$, $A = Q\Lambda Q^{-1}$, or when applying weights $W$ to rows of $A$ (compute $WA$).

Unfortunately you do not realize that instead of a diagonal matrix $W$ you have a vector of diagonal elements $\begin{bmatrix}w_{11},\dots,w_{nn}\end{bmatrix}$.

In [2]:
w = rand(3)
A = rand(3,3)

w*A # Dimension error!

LoadError: DimensionMismatch("A has dimensions (3,1) but B has dimensions (3,3)")

It is tempting to start transposing things. If you do this, you might stumble on the expression
$$w^\top A$$
which runs but is not at all what you intended!
What is $w^\top A$? It's a row vector of length n.

### The cascade of errors
Instead of an $n\times n$ matrix, you have a vector in $\mathbb{R}^n$. If you don't catch this now, your code is going to get more and more difficult to manage. Matrices will be the wrong sizes. Results will look weird. Soon you will be hopelessly confused!<br>
But you have one more chance to recover. When you notice your code no longer matches your expectations...

$$\textbf{STOP!}$$

Back up to the first error and don't proceed until you understand why it occurred.

### Some troubleshooting tips:
* When solving a problem on paper, write down the sizes of your variables before starting the problem.
* When implementing your solution, print the sizes of matrices you import from a JSON file
* When implementing a long computation, print the sizes of intermediate values. In Example 2 above, you could detect the $w^\top A$ error by checking its size and realizing it is no longer a matrix.
* Use `println("size A ", size(A))` or `println("Size A is correct: ", size(A) == (m,n))`. It's fine to turn in code containing these debugging lines.

## 2. Decomposition Confusion
Both TAs and students are guilty of confusing whether `svd(A)` returns `U, S, V` or `U, S, Vt`, possibly because the documentation is confusing. But there is no reason to stay confused. Just check!

In [3]:
A = rand(3,3)
U, S, V = svd(A)
# I don't know if my V variable contains V or Vᵀ
# Instead of wasting time trying to Google it I will just compute UΣVᵀ and compare it with A
norm(U*diagm(S)*V - A)

1.2632317845821166

In [4]:
# I know UΣVᵀ = A, so I probably confused V and Vᵀ
norm(U*diagm(S)*V' - A)
# Now I know my V variable contains V, not Vᵀ

6.13925476028306e-16

## 3. Type Confusion
Occasionally you will have trouble with Integer and Float data types.
For example, you use a floating point value as an index and receive `ArgumentError: invalid index: 1.0 of type Float64`.

There's an easy way to solve this: just convert your float to an integer.

In [5]:
t = 1.0
a = rand(10)
# a[t] # Invalid index 1.0 of type Float64
a[Integer(t)] # works

0.11971034446009843

### InexactError
Now suppose you are doing some computation to find $t$. You have $t=1.5$ but you know it should be truncated to $t=1$. Calling `Integer(t)` will no longer work because `Integer`, on its own, will not truncate the 0.5.

In [6]:
t = 1.5
# a[Integer(t)] # InexactError: Int64(1.5)
a[Integer(floor(t))] # This looks messy but works

0.11971034446009843

### More dots = better code
Sometimes you will see an InexactError and be unsure why. This often occurs because some of your data is Integer-typed when it should really be Float.
How does this happen?
* The data in the JSON file was Integer-typed. If you print the data, you will see it has type Int. You can convert a vector or matrix $A$ to float by calling `A = Float64.(A)` (note the broadcasting dot!)
* You constructed an Integer-typed matrix. For example, you constructed $A = \begin{bmatrix}1 & 2 \\ 0 & 1\end{bmatrix}$ like this:

In [7]:
A = [1 2
     0 1]

2×2 Matrix{Int64}:
 1  2
 0  1

It's good practice to add a decimal point, indicating that the values of $A$ are floating-point numbers. (Here we added decimal points on all 4 elements, but you only need a single element to ensure $A$ has type `Float64`.)

In [8]:
A = [1. 2.
     0. 1.]

2×2 Matrix{Float64}:
 1.0  2.0
 0.0  1.0

Adding the decimal point where you intend to use floating-point numbers protects you from confusing `InexactError`s.

## 4. Restart Your Jupyter Notebook
If you see weird behavior, it's likely you have lots of unused variables in your notebook. For example, you define a variable `s = 1`, then decide you should have called it `s_i`. So you change all the `s`'s to `s_i` in your code...but of course you miss one.

Just because you stopped having the line `s = 1` in your Jupyter notebook does not mean `s` was deleted from the notebook memory. Your code continues to run, but produces wrong results. To clear `s`, **restart your notebook.**<br>
Once you do this, you'll get a crash where the now-undefined variable `s` is used. You'll easily catch the error and replace `s` with `s_i`.

When to restart your notebook:
* You can't find a bug
* You see something "weird" or inexplicable
* You get a memory error
* Your code is ready to turn in. At this point you should be able to restart, re-run and get exactly the same results. If you don't, your code is likely using a variable that exists in the notebook's memory but isn't defined (for example you write `s = 1`, run the cell, then delete the line later). This will be a major headache if the graders need to evaluate your code.

## 5. Modifying Data / Overwriting Variables
In problem 5 on the midterm some students turned in images that had several filters applied. This made it difficult to evaluate the correctness of their work. To save yourselves and us the headache, please be careful when overwriting variables and avoid unintentionally modifying data.

In [9]:
# let's pretend we have some data from a JSON file
data = Dict("A"=>rand(3,3), "n"=>4)

A = data["A"] # implicitly we copy A
n = data["n"] # and n

4

In [10]:
# In part of our code, we modify A. It's OK to overwrite A if you're careful.
A += I

3×3 Matrix{Float64}:
 1.88201    0.909204  0.252519
 0.0589962  1.27832   0.958962
 0.290077   0.383319  1.45554

In [11]:
# In the next part we need A alone, not A + I
# RELOAD A from data["A"] to ensure it is correct.
A = data["A"]

3×3 Matrix{Float64}:
 0.882006   0.909204  0.252519
 0.0589962  0.278316  0.958962
 0.290077   0.383319  0.455537

## 6. "Efficiency"
Some students worry about writing "efficient" code in the sense that it runs fast, avoids unnecessary memory allocations, or is particularly elegant.<br>
**There is no expectation in EE263 to write "efficient" code.**<br>
"Efficiency", in the sense of saving processor cycles, often goes hand-in-hand with debugging headaches, unmaintainability, confusingness, and other undesirable code traits.

Things you will not lose points for:
* Code that is repetitive but correct
* Code that uses `push!` to grow a list instead of pre-allocating enough space
* Code that uses `for` loops instead of broadcasting/summing
* Code with "debugging" lines and print statements
* Code that runs slowly but correctly[<sup>1</sup>](#fn1)

Things you will lose points for:
* Code that does not produce the right answer

### In EE263 the best code is the one that is easy to read, write, and debug.

<span id="fn1"> 1. If your code runs so slowly that it does not produce an answer before the exam is due, this is a symptom of a larger error.</span>

## Ask For Help
During the exam, we cannot help you debug your code but we can provide some assistance. Don't be afraid to ask. The worst thing we might say is 'sorry, we can't help' which is the default outcome if you don't ask. Please email us :)

Some reasons to email during the exam
* Code we provided does not run
* You are having trouble importing a standard library, such as `Plots`.
* You suffered a serious and unexpected computer problem, such as a hard disk failure or Windows suddenly deciding to spend 8 hours updating (Please back up your work and try to avoid these types of issues.)
* You are writing a lot of really messy, error-prone code (reexamine your assumptions about the problem!)

Make sure to include a screenshot of your code and any error messages. Otherwise we will not understand the issue.